In [2]:
import numpy as np
import pandas as pd
import seaborn as sns
import folium
from folium import plugins

## Example data

In [3]:
df_population = pd.read_csv('data/Population Data.csv')
city_coords = df_population[['Lat','Lon']].values

In [4]:
city_coords[:3]

array([[  36.0122, -115.0375],
       [  42.9847,  -71.4439],
       [  40.6663,  -74.1935]])

### EasyMap

In [5]:
def easy_map(coords):
    """Make a marker for each (lat, long) pair. Plot on a map
    centered by the average position. """
    center = coords.mean(axis = 0)
    m = folium.Map(location = center, zoom_start=3.4)
    for i, coord in enumerate(coords):
        tooltip=f"{i}"
        folium.Marker(
            list(coord), tooltip=tooltip
        ).add_to(m)
    
    return m

In [6]:
easy_map_ex = easy_map(city_coords)
easy_map_ex

In [7]:
easy_map_ex.save('output/easy_map_example.html')

### Timestamped Temperature Map

#### Import data and do required data manipulation
We need to turn these two tables from the bp_weather challenge into the GeoJSON format, so we can use them in a TimestampedGeoJson map. 

In [6]:
## Import city-temp vs. time df
df_daily_temp_by_city = pd.read_csv('data/daily_temps_interpolated.csv')

In [7]:
df_daily_temp_by_city.head(2)

Unnamed: 0    datetime                                  Henderson, Nevada  \
0           0  2015-01-01  (2.8042193135220215, -1.06443748149932, 7.8955...   
1           1  2015-01-02  (3.5833611965500256, -1.6416043119829218, 9.48...   

                           Manchester, New Hampshire  \
0  (-2.0414172014848404, -5.2967596261279555, 0.8...   
1  (1.8123476273733083, -0.4878899169065774, 4.51...   

                               Elizabeth, New Jersey  \
0  (0.7271640854069779, -2.220666115556862, 3.413...   
1  (3.6269191023738485, 1.5579536595154981, 5.636...   

                                  Newark, New Jersey  \
0  (0.721623158787829, -2.219899178588003, 3.3984...   
1  (3.632688786895376, 1.576935014315009, 5.63197...   

                                Paterson, New Jersey  \
0  (0.7451333314337338, -2.249080056243332, 3.489...   
1  (3.5967672015962546, 1.4627489512318697, 5.664...   

                             Jersey City, New Jersey  \
0  (0.7012627531441941, -2.2070541621717514, 3.33...   
1  (3.6583143659774557, 1.659695936931595, 5.6106...   

                             Albuquerque, New Mexico  \
0  (-3.5077581597478513, -7.620209751439084, 0.50...   
1  (-1.6105225388897615, -6.293151018732043, 4.47...   

                                   Buffalo, New York  ...  \
0  (-3.254167638382994, -6.70000884781188, 1.5518...  ...   
1  (-1.5874865803073686, -4.9999691405260025, 4.4...  ...   

                                    Miramar, Florida  \
0  (7.261264629068813, 1.248439289328133, 13.3052...   
1  (11.946649279284825, 8.531744135775167, 15.040...   

                                    Hialeah, Florida  \
0  (7.267839188054266, 1.2597305417711855, 13.306...   
1  (11.964299921129687, 8.54262383433644, 15.0643...   

                              Coral Springs, Florida  \
0  (7.201354121181819, 1.154658288185659, 13.2794...   
1  (11.84453325605251, 8.456272588337987, 14.9129...   

                              Miami Gardens, Florida  \
0  (7.243316298738815, 1.2219635019938928, 13.294...   
1  (11.926497144776375, 8.513341986493058, 15.018...   

                                      Miami, Florida  \
0  (7.258345407380921, 1.246744173453674, 13.2989...   
1  (11.960202600064934, 8.53553492156532, 15.0627...   

                                  Hollywood, Florida  \
0  (7.2134740706337235, 1.1762319103059715, 13.28...   
1  (11.88196168021216, 8.478299895369968, 14.9645...   

                            Fort Lauderdale, Florida  \
0  (7.192921258888248, 1.143997576015988, 13.2713...   
1  (11.846530507310883, 8.452247756304931, 14.920...   

                              Pompano Beach, Florida  \
0  (7.1745562775268095, 1.1151363386505413, 13.26...   
1  (11.814495652370088, 8.428817579069989, 14.880...   

                            West Palm Beach, Florida  \
0  (7.093912585440351, 0.9870844318322061, 13.232...   
1  (11.66533322685168, 8.322509004465156, 14.6904...   

                                         daily_temps  
0  (2.226442692178053, -1.988541139572663, 6.4489...  
1  (4.4438566903907, 0.808315671731891, 8.2566831...  

[2 rows x 288 columns]

In [8]:
# Evaluate the inner tuples, so they're no longer strings
from ast import literal_eval
for i in range(2, len(df_daily_temp_by_city.columns)):
    df_daily_temp_by_city.iloc[:,i] = df_daily_temp_by_city.iloc[:,i].apply(lambda x: literal_eval(x))

In [9]:
df_daily_temp_by_city.head(3)

Unnamed: 0    datetime                                  Henderson, Nevada  \
0           0  2015-01-01  (2.8042193135220215, -1.06443748149932, 7.8955...   
1           1  2015-01-02  (3.5833611965500256, -1.6416043119829218, 9.48...   
2           2  2015-01-03  (5.313746601456074, 0.0537208688345699, 11.180...   

                           Manchester, New Hampshire  \
0  (-2.0414172014848404, -5.2967596261279555, 0.8...   
1  (1.8123476273733083, -0.4878899169065774, 4.51...   
2  (-1.5042004354211351, -4.641065832081684, 3.01...   

                               Elizabeth, New Jersey  \
0  (0.7271640854069779, -2.220666115556862, 3.413...   
1  (3.6269191023738485, 1.5579536595154981, 5.636...   
2  (1.9401067861655703, -0.10967571559474101, 5.0...   

                                  Newark, New Jersey  \
0  (0.721623158787829, -2.219899178588003, 3.3984...   
1  (3.632688786895376, 1.576935014315009, 5.63197...   
2  (1.9366071662619093, -0.09493625703022997, 5.0...   

                                Paterson, New Jersey  \
0  (0.7451333314337338, -2.249080056243332, 3.489...   
1  (3.5967672015962546, 1.4627489512318697, 5.664...   
2  (1.9531350402008636, -0.18257317909691917, 5.0...   

                             Jersey City, New Jersey  \
0  (0.7012627531441941, -2.2070541621717514, 3.33...   
1  (3.6583143659774557, 1.659695936931595, 5.6106...   
2  (1.9230983187361383, -0.031069294684709044, 5....   

                             Albuquerque, New Mexico  \
0  (-3.5077581597478513, -7.620209751439084, 0.50...   
1  (-1.6105225388897615, -6.293151018732043, 4.47...   
2  (-1.5629823097813513, -8.72259919416442, 5.303...   

                                   Buffalo, New York  ...  \
0  (-3.254167638382994, -6.70000884781188, 1.5518...  ...   
1  (-1.5874865803073686, -4.9999691405260025, 4.4...  ...   
2  (-0.6332781996894676, -5.599949953882896, 8.30...  ...   

                                    Miramar, Florida  \
0  (7.261264629068813, 1.248439289328133, 13.3052...   
1  (11.946649279284825, 8.531744135775167, 15.040...   
2  (13.882819669538627, 11.613471883752727, 17.38...   

                                    Hialeah, Florida  \
0  (7.267839188054266, 1.2597305417711855, 13.306...   
1  (11.964299921129687, 8.54262383433644, 15.0643...   
2  (13.898439749637344, 11.627892569102757, 17.39...   

                              Coral Springs, Florida  \
0  (7.201354121181819, 1.154658288185659, 13.2794...   
1  (11.84453325605251, 8.456272588337987, 14.9129...   
2  (13.776804282038322, 11.520199220572357, 17.27...   

                              Miami Gardens, Florida  \
0  (7.243316298738815, 1.2219635019938928, 13.294...   
1  (11.926497144776375, 8.513341986493058, 15.018...   
2  (13.857516482265105, 11.59230860429814, 17.355...   

                                      Miami, Florida  \
0  (7.258345407380921, 1.246744173453674, 13.2989...   
1  (11.960202600064934, 8.53553492156532, 15.0627...   
2  (13.889114398533502, 11.620959646627288, 17.38...   

                                  Hollywood, Florida  \
0  (7.2134740706337235, 1.1762319103059715, 13.28...   
1  (11.88196168021216, 8.478299895369968, 14.9645...   
2  (13.808623920967795, 11.549958815046766, 17.30...   

                            Fort Lauderdale, Florida  \
0  (7.192921258888248, 1.143997576015988, 13.2713...   
1  (11.846530507310883, 8.452247756304931, 14.920...   
2  (13.772007402977584, 11.517701465200151, 17.26...   

                              Pompano Beach, Florida  \
0  (7.1745562775268095, 1.1151363386505413, 13.26...   
1  (11.814495652370088, 8.428817579069989, 14.880...   
2  (13.73905655470369, 11.488634166796466, 17.230...   

                            West Palm Beach, Florida  \
0  (7.093912585440351, 0.9870844318322061, 13.232...   
1  (11.66533322685168, 8.322509004465156, 14.6904...   
2  (13.589111450096825, 11.35548016535289, 17.081...   

                                         daily_temps  
0  (2.2

In [10]:
df_pop = pd.read_csv('data/Population Data.csv')

In [11]:
df_pop.head(3)

City          State  population       Lon      Lat
0   Henderson         Nevada      260068 -115.0375  36.0122
1  Manchester  New Hampshire      109830  -71.4439  42.9847
2   Elizabeth     New Jersey      125660  -74.1935  40.6663

#### Data Manipulation to transform data into mappable format

In [12]:
def citystate_to_latlong(df_pop, continental_only = False):
    """Builds a map between 'City, State' and (Lon, Lat). """
    cs_latlong = {}
    for row in df_pop[['City', 'State', 'Lon', 'Lat']].values:
        if row[1] in {"Alaska", "Hawaii"} and continental_only == True:
            continue
        cs_latlong[f"{row[0]}, {row[1]}"] = (row[2], row[3])
        
    return cs_latlong

def citystate_to_temps(df_daily_temp_by_city, citystate_latlong):
    """Build a map between 'City, State' and temps [T_0, T_1, ..., T_N]"""
    cs_temps = {}
    for k, v in citystate_latlong.items():
        cs_temps[k] = [t[0] for t in df_daily_temp_by_city[k].values]
    return cs_temps

In [13]:
class TemperatureTimeSeries:
    """Class to simplify working with city locations and temperature timeseries."""
    def __init__(self, city_to_coord, city_daily_temps):
        self.city_to_coord = city_to_coord
        self.city_daily_temps = city_daily_temps
        self.coords =[[c[1], c[0]] for c in list(city_to_coord.values())]
        self.temp_vals = list(city_daily_temps.values())
        
        self.times = list(range(0, len(self.temp_vals[0])))
        self.normalization_vals = (-100, 100)
        
        
    def transform_for_heatmap(self, normalized = None):
        """Desired: 
        [ [[lat_a, long_a, T_a0], ... [lat_z, long_z, T_z0]],
            ...
            [[lat_a, long_a, T_aN], ... [lat_z, long_z, T_zN]] ] """
        spatial_temps_over_time = []

        for t in self.times:
            pos_with_temps = []
            for i, (lat, long) in enumerate(self.coords):
                if normalized is None:
                    pos_with_temps.append([lat, long, self.temp_vals[i][t]])
                else:
                    pos_with_temps.append([lat, long, self.normalize(temp_vals[i][t])])
                    
                    
            spatial_temps_over_time.append(pos_with_temps)
            
        return spatial_temps_over_time
    
    def normalize(self, x):
        normed = (x - self.normalization_vals[0])/ (self.normalization_vals[1] - self.normalization_vals[0])
        return normed

In [14]:
cs_latlong =  citystate_to_latlong(df_pop, continental_only=True)
cs_temps = citystate_to_temps(df_daily_temp_by_city, cs_latlong)
temp_tseries = TemperatureTimeSeries(cs_latlong, cs_temps)

In [15]:
# Make a big 3D array of size (num_datetimes x num_cities x 3), inner elements are
# (lat, long, Temperature) for a given datetime.
spatial_temps_by_time = temp_tseries.transform_for_heatmap()
times = df_daily_temp_by_city.datetime.values

In [16]:
spatial_temps_by_time[1000][:5]

[[36.0122, -115.0375, 24.703133804533174],
 [42.9847, -71.4439, 24.069181039905118],
 [40.6663, -74.1935, 24.15627980674224],
 [40.7242, -74.1726, 24.145130241772787],
 [40.9147, -74.1628, 24.20865156174733]]

In [17]:
# The 1000th element of spatial_temps_by_time corresponds to datetime:
times[1000]

'2017-09-27'

In [18]:
def make_heatmap(data):
    """Make heatmap across time, which takes in an array of arrays of [lat,long,value],
    using HeatMapWithTime. NOTE: Weights must be small numbers (between 0 and 2?)."""
    print(f"Number of times = {len(data)}.")
    print(f"Number of positions = {len(data[0])}.")
    # Max temperature = 50
    
    coords = np.array([d[:2] for d in data[0]])
    
    center = coords.mean(axis = 0)
    m = folium.Map(location = center, zoom_start=3.4)
    # Make heatmap...
    hm = plugins.HeatMapWithTime(data, auto_play=True,max_opacity=0.8, max_speed=1000, radius = 5)

    hm.add_to(m)
    return m

This heatmap works, but I'm actually looking for a chloropleth, since heatmaps will add up the temperatures (so dense regions will always look "hot"). Another solution is to just plot points in time on a map, with color determined by temperature. 

Can do this using folium's TimestampedGeoJson.

In [19]:
# This sets the minimum and maximum temperatures, as well as the bin-width for visualization
temp_bins = list(range(-20, 45, 1))
color_scale = sns.color_palette("coolwarm", len(temp_bins)).as_hex()

In [20]:
print(len(temp_bins), len(color_scale))

65 65


In [21]:
def color_coding(poll, bin_edges):    
    idx = np.digitize(poll, bin_edges, right=True)
    try:
        color = color_scale[idx]
    except:
        color = color_scale[-1]

    return color

In [22]:
color_coding(50, temp_bins)

'#b8122a'

In [23]:
# Use TimestampedGeoJson(data)
# Inspired by: https://towardsdatascience.com/visualizing-air-pollution-with-folium-maps-4ce1a1880677
def generate_geojson_features(spatial_temps_by_time, times, temp_edges):
    """
    This transforms this data, along with timestamps into a GeoJSON
    format (list of feature dictionaries), so it can be passed to 
    folium.plugins.TimestampedGeoJson().
    """
    print('> Creating GeoJSON features...')
    features = []
    for t_i, spatial_temps in enumerate(spatial_temps_by_time):
        # This is all [lat,long,T] at t=t_i
        for (lat, long, T) in spatial_temps:
            time = times[t_i]
            # Temp to color
            color =  color_coding(T, temp_edges)
            feature = {
                'type': 'Feature',
                'geometry': {
                    'type':'Point', 
                    'coordinates':[long, lat]
                },
                'properties': {
                    'time': time,
                    'style': {'color' : color},
                    'icon': 'circle',
                    'iconstyle':{
                        'fillColor': color,
                        'fillOpacity': 0.8,
                        'stroke': 'true',
                        'radius': 7
                    }
                }
            }
            features.append(feature)
        
    return features

In [25]:
# Use the times from the dataframe, build 1 year (365 days) worth,
# 6 years worth is 670k points and won't render.
n_first = 365
geo_features = generate_geojson_features(spatial_temps_by_time[:n_first:10], times[:n_first:10], temp_bins)

> Creating GeoJSON features...


2020 Temperature map data

In [26]:
n_begin = 365*5 # (skip 2015-2019)
n_end = 365*6
geo_features =  generate_geojson_features(spatial_temps_by_time[n_begin:n_end:10], times[n_begin:n_end:10], temp_bins)

> Creating GeoJSON features...


In [27]:
geo_features[-1]

{'type': 'Feature',
 'geometry': {'type': 'Point', 'coordinates': [-80.1266, 26.7483]},
 'properties': {'time': '2020-12-25',
  'style': {'color': '#b5cdfa'},
  'icon': 'circle',
  'iconstyle': {'fillColor': '#b5cdfa',
   'fillOpacity': 0.8,
   'stroke': 'true',
   'radius': 7}}}

In [28]:
# Make GeoJSON vs Time map
from folium import plugins
def map_timestamped_GeoJSON(features, transition_time = 200, max_speed=10000):
    """Make GeoJSON map, from a list of GeoJson features."""
    print(f"Total number of points: {len(features)}")
    
    center = [39.5, -98.35] # Center of continental US
    temp_timemap = folium.Map(location=center, zoom_start=4, prefer_canvas=True)

    plugins.TimestampedGeoJson(
        {'type': 'FeatureCollection', 'features': features}, 
        max_speed=max_speed, transition_time=transition_time).add_to(temp_timemap)
    
    return temp_timemap

In [29]:
temp_timemap = map_timestamped_GeoJSON(geo_features)

Total number of points: 10471


In [30]:
temp_timemap

In [31]:
temp_timemap.save('output/temperature_vs_time_2020.html')

In [32]:
# Color map varies from -20 to 40 degrees.
sns.color_palette("coolwarm", 17)

[(0.29471843211764703, 0.39354192974117647, 0.8343841671215686),
 (0.3634607953411765, 0.4847836818509804, 0.9010188868941177),
 (0.4358148063058824, 0.5707073031529412, 0.951717381282353),
 (0.5108243242509803, 0.6493966148235294, 0.9850787763764707),
 (0.5923558594980393, 0.7227920292549019, 0.9994338748235294),
 (0.6672529243333334, 0.7791764569999999, 0.992959213),
 (0.7388259949411764, 0.8225716218235294, 0.9682610638235294),
 (0.8049647588235295, 0.8516661605568627, 0.9261650744313725),
 (0.8674276350862745, 0.864376599772549, 0.8626024620196079),
 (0.9193759889058823, 0.8312727235294118, 0.7828736304470588),
 (0.9527607176705882, 0.7829647976, 0.6986457713058823),
 (0.968203399, 0.7208441, 0.6122929913333334),
 (0.9660167198392157, 0.6461297415882352, 0.5258903482588235),
 (0.9440545734235294, 0.5531534787490197, 0.4355484903137255),
 (0.9057834780117647, 0.4551856921647059, 0.35533588384705883),
 (0.8523781350078431, 0.34649194649411763, 0.2803464686980392),
 (0.7851533046784314, 0.2208510887215686, 0.21167287700784312)]